## Load Required Libraries

In [1]:
#libraties
import bs4
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
import csv
import time
from datetime import datetime

## Web Scrapping

In [2]:
# loading pages 1-25 from confessions
url = 'https://www.uberpeople.net/forums/confessions/'
confpages = []
maxpages = 25
for number in range(1,maxpages+1):
    url_page = url
    page = 'page-'+str(number)   
    url_use = ''.join([url_page, page])  
    confpages.append(url_use)

In [3]:
confpages

['https://www.uberpeople.net/forums/confessions/page-1',
 'https://www.uberpeople.net/forums/confessions/page-2',
 'https://www.uberpeople.net/forums/confessions/page-3',
 'https://www.uberpeople.net/forums/confessions/page-4',
 'https://www.uberpeople.net/forums/confessions/page-5',
 'https://www.uberpeople.net/forums/confessions/page-6',
 'https://www.uberpeople.net/forums/confessions/page-7',
 'https://www.uberpeople.net/forums/confessions/page-8',
 'https://www.uberpeople.net/forums/confessions/page-9',
 'https://www.uberpeople.net/forums/confessions/page-10',
 'https://www.uberpeople.net/forums/confessions/page-11',
 'https://www.uberpeople.net/forums/confessions/page-12',
 'https://www.uberpeople.net/forums/confessions/page-13',
 'https://www.uberpeople.net/forums/confessions/page-14',
 'https://www.uberpeople.net/forums/confessions/page-15',
 'https://www.uberpeople.net/forums/confessions/page-16',
 'https://www.uberpeople.net/forums/confessions/page-17',
 'https://www.uberpeopl

In [5]:
urllist = []
for oneurl in range(len(confpages)):
    page = requests.get(confpages[oneurl], headers = {'User-Agent': 'Mozilla/5.0'})
    
    soup = BeautifulSoup(page.text, 'html.parser')
    url_require = soup.find_all(class_ = "structItem-title")
    
    
    for url in url_require:
        link = url.find('a')['href']
        urllist.append(link) 

In [6]:
urllist

['/threads/break-out-your-fancy-dress-mildred.445671/',
 '/threads/ants-smoking-lung-darts.261337/',
 '/threads/made-an-epic-move-to-save-2-miles-and-4-minutes.445542/',
 '/threads/pro-tip-go-offline-when-filling-up-after-baked-pax.282096/',
 '/threads/absolute-worse.445442/',
 '/threads/getting-back-to-normal.445339/',
 '/threads/no-you-dont-get-to-make-me-wait-10-minutes-on-a-scheduled-ride.439285/',
 '/threads/post-your-most-interesting-ridiculous-or-mind-blowing-app-screenshots.444936/',
 '/threads/chicago-driver-vs-rider.444373/',
 '/threads/driving-ms-winifred.445036/',
 '/threads/wow-got-five-girls-in-two-months-45hr-w-lyft.445357/',
 '/threads/17-years-old-girl-stabbed-female-uber-driver-do-you-ever-feel-unsafe-with-female-passengers.445434/',
 '/threads/dont-judge-a-book-by-its-cover.420582/',
 '/threads/heavy-concert-traffic-no-tip-special.445317/',
 '/threads/eviction-day-ride.445157/',
 '/threads/come-to-my-bungalow.444683/',
 '/threads/apparently-my-market-is-larger-than-i

In [7]:
#within the forum soup
def processPage(url_link):
    time_post = []
    page_data = requests.get(url_link, {'User-Agent': 'Mozilla/5.0'})
    borsch_page = BeautifulSoup(page_data.content, 'html.parser')
    metaData = borsch_page.find_all(class_= "message-content js-messageContent" )
    for t in range(len(metaData)):
        text = metaData[t]
        message = ''
        post = text.find(class_="bbWrapper")
        for child in post.children:
            if type(child)!=bs4.element.Tag:
                message += str(child.string) if child.string else ''
    
        desc = text.find(class_ = "message-userContent lbContainer js-lbContainer")
        name, time = desc['data-lb-caption-desc'].split(' · ')
        
        message_id = desc['data-lb-id']
        time_post.append((message_id, name, time, message))#, desc, post))
        
    return time_post

In [8]:
# ** define our data processing function
DEBUG_single_pages = []
def processTopic(url_link):
    ''' take the URL from the list we collected '''
    
    site = 'https://www.uberpeople.net'
    url = url_link
    seq = (site,url)
    page = ''.join(seq)
    
    headers = {'User-Agent': 'Mozilla/5.0'}
    page_s = requests.get(page, headers = headers)
    borsch = BeautifulSoup(page_s.content, 'html.parser')
        
    topic = []
    pages_for_loop = borsch.find(class_="pageNavSimple-el pageNavSimple-el--current")
    try:
        loop_times = str(pages_for_loop).split()[-2]
        list_of_pages = range(1,int(loop_times)+1)
        # define where store info
    except:
        list_of_pages = [1]
        DEBUG_single_pages.append(f'{site}{url}')

        
    pages = []
    for page_num in list_of_pages:
        pages.append(processPage(f'{site}{url}page-{page_num}'))

    topic = [message for page in pages for message in page]
    return(topic)

In [9]:
%%time 
total_length = 0
topics_dict = {}
for url_short in urllist:
    topics_dict[url_short] = processTopic(url_short)
    total_length += len(topics_dict[url_short])

Wall time: 36min 38s


In [10]:
# data dictionary
topics_dict

{'/threads/break-out-your-fancy-dress-mildred.445671/': [('post-7142367',
   'The Gift of Fish',
   'Jul 15, 2021 at 8:12 PM',
   "... we're going to Sizzler cos we got some celebratin' to do! \n\n\n\n\nIf I go online and win this extra dollar bonus, what do I spend it on? What would you spend it on? Would you go wild and spend it all at once or would you be prudent and save some of it for a rainy day?\n\nDecisions, decisions, decisions."),
  ('post-7142380',
   'Illini',
   'Jul 15, 2021 at 8:21 PM',
   'Nice, but not as not nice as my 50 cent bonus for giving an Uber Green ride.'),
  ('post-7142402',
   'The Gift of Fish',
   'Jul 15, 2021 at 8:37 PM',
   "Minibonus winner! How low can they go? 50 cents is the lowest I've seen yet. Most impressive.\n\n"),
  ('post-7142536',
   'Another Uber Driver',
   'Jul 15, 2021 at 10:25 PM',
   'I got one of those half dollar bonuses Tuesday. .'),
  ('post-7142581',
   'Judge and Jury',
   'Jul 15, 2021 at 11:02 PM',
   'Mildred? Yeah, right.\n\

## Creating Dataframe from scrape data

In [11]:
df3 = pd.concat({k: pd.Series(v) for k, v in topics_dict.items()}).reset_index()

In [12]:
df3= df3.rename(columns={"level_0": "col1", "o": "col2"})

In [13]:
df4 = df3

In [14]:
# remove comments on each stories and keep actual story
df4 = df4.drop_duplicates(subset='col1', keep="first")

In [15]:
df4

col1  level_1  \
0      /threads/break-out-your-fancy-dress-mildred.44...        0   
16              /threads/ants-smoking-lung-darts.261337/        0   
73     /threads/made-an-epic-move-to-save-2-miles-and...        0   
85     /threads/pro-tip-go-offline-when-filling-up-af...        0   
111                      /threads/absolute-worse.445442/        0   
...                                                  ...      ...   
23694  /threads/the-road-a-driver%E2%80%99s-diary-our...        0   
23705  /threads/wow-just-now-i-got-a-gift-from-uber-a...        0   
23716         /threads/get-out-of-jail-free-card.407051/        0   
23719  /threads/super-hero-uberman-tip-%F0%9F%A6%B8%E...        0   
23747               /threads/weird-food-delivery.406989/        0   

                                                       0  
0      (post-7142367, The Gift of Fish, Jul 15, 2021 ...  
16     (post-3955413, ftupelo, May 19, 2018 at 7:39 P...  
73     (post-7139982, June132017, Jul 14, 2021 at 1:2...  
85     (post-4277390, MadTownUberD, Sep 2, 2018 at 4:...  
111    (post-7137806, Bojingles, Jul 12, 2021 at 5:15...  
...                                                  ...  
23694  (post-5009596, Reager, May 16, 2019 at 2:13 AM...  
23705  (post-6396293, Young Kim, Jul 23, 2020 at 5:44...  
23716  (post-6396821, SleelWheels, Jul 23, 2020 at 9:...  
23719  (post-6392408, Mkang14, Jul 22, 2020 at 4:26 A...  
23747  (post-6395388, The Jax, Jul 23, 2020 at 11:10 ...  

[875 rows x 3 columns]

In [16]:
df5= pd.Series(df4[0]) 

In [17]:
data =df5.apply(pd.Series) # column 2
data.head()

0                 1                        2  \
0    post-7142367  The Gift of Fish  Jul 15, 2021 at 8:12 PM   
16   post-3955413           ftupelo  May 19, 2018 at 7:39 PM   
73   post-7139982        June132017  Jul 14, 2021 at 1:27 AM   
85   post-4277390      MadTownUberD   Sep 2, 2018 at 4:52 PM   
111  post-7137806         Bojingles  Jul 12, 2021 at 5:15 PM   

                                                     3  
0    ... we're going to Sizzler cos we got some cel...  
16   Howdy all you Ants! On this episode of I'd lik...  
73   A guy named Russel ordered a Lyft. So looking ...  
85   Maybe it was the fact that my car smelled like...  
111  My account has never been placed on hold for a...

In [18]:
data1= data.rename(columns={"0": "Post", "1": "Name","2": "Datetime","3": "Story"})

In [19]:
data1 = data

In [20]:
data1.columns = ['Post', 'Name', 'Datetime', 'Story']

In [21]:
#data cleaninf
data1['Story'].replace('', np.nan, inplace=True)
data1.dropna(subset=['Story'], inplace=True)

### Final  Dataset from 2017-2021

In [22]:
# Split month into a separate column
data1['year']= pd.DatetimeIndex(data1['Datetime']).year


In [23]:
data1.to_csv('Story.csv', index=False)


### Data for 2020

In [24]:
# selecting rows for 2020
data_2020 = data1[data1['year'] == 2020]

In [25]:
data_2020.to_csv('data_2020.csv', index=False)


### Data for 2021

In [26]:
# selecting rows for 2021
data_2021 = data1[data1['year'] == 2021]

In [27]:
data_2021.to_csv('data_2021.csv', index=False)